# Compton Analysis Notebook

In [5]:
ANGLES_OUTPUT_PATH = r"G:\.shortcut-targets-by-id\1IcR20O5deY8V-HZhJrHf7ZL2cmAiG7GY\ComptonMeasurements\Angles"
ENERGY_CHANNEL_CALIBRATION_PATH = r"G:\.shortcut-targets-by-id\1IcR20O5deY8V-HZhJrHf7ZL2cmAiG7GY\ComptonMeasurements\EnergyChannel"
MCA_FILE_EXTENSION = ".mca"
MCA_FIRST_NON_ZERO_CHANNEL = 568

%load_ext autoreload
%autoreload 2

In [6]:
import os
import pathlib
import mca_output
import plotly_utils

def find_mca_files_in_folder(folder: str) -> list[pathlib.Path]:
    folder_path = pathlib.Path(folder)
    return [pathlib.Path.joinpath(folder_path, out_file) for out_file in os.listdir(folder) if pathlib.Path(out_file).suffix == MCA_FILE_EXTENSION]

# Find all MCA files in given folder
if not os.path.exists(ANGLES_OUTPUT_PATH) or not os.path.isdir(ANGLES_OUTPUT_PATH):
    raise FileNotFoundError(f"Directory \"{ANGLES_OUTPUT_PATH}\" does not exist")

angle_calibration_mca_files = find_mca_files_in_folder(ANGLES_OUTPUT_PATH)
angle_calibration_mca_outs = [mca_output.parse_output_file(mca_file.absolute()) for mca_file in angle_calibration_mca_files]


In [7]:
for mca_out_file in angle_calibration_mca_outs:
    fig = plotly_utils.generate_mca_out_figure(mca_out_file, pathlib.Path(mca_out_file.path).stem)
    fig.show()

### Extract Maximum Intensity for Each Angle

The following excerpt extracts the bin with the highest count number around the 3000 region.

In [8]:
import numpy as np

for mca_out_file in angle_calibration_mca_outs:
    channel_count = np.array(mca_out_file.channel_count_list, np.float32) / mca_out_file.measurement_time
    max_index = np.argmax(channel_count)
    max_counts = channel_count[max_index]
    print(f"{pathlib.Path(mca_out_file.path).stem}: channel: {max_index}, counts: {max_counts}")

angle_2.5: channel: 2916, counts: 163.4600067138672
angle_-10: channel: 2844, counts: 12.600000381469727
angle_7.5: channel: 2930, counts: 182.10000610351562
angle_5: channel: 2930, counts: 177.69000244140625
angle_0: channel: 2930, counts: 134.7899932861328
angle_20: channel: 2894, counts: 51.5099983215332
angle_-5: channel: 2891, counts: 64.52999877929688
angle_25: channel: 2870, counts: 6.869999885559082
angle_15: channel: 2912, counts: 124.7300033569336
angle_10: channel: 2920, counts: 173.4499969482422
angle_-15: channel: 2833, counts: 0.9300000071525574


We can see from the above that indeed at the angle 7.5 degrees the most counts per unit time (100s live time) is measured at around bin 2930.

### Fitting a Gaussians for Compton Spectrum & Gamma Decay Peak

In [9]:
import typing
import curve_fitter
import analysis_utils

filter_7_5_measurement: typing.Callable[[mca_output.MCAOutput], bool] = lambda mca_out: pathlib.Path(mca_out.path).stem == "angle_7.5"
targetless_7_5_measurement = next((mca_out for mca_out in angle_calibration_mca_outs if filter_7_5_measurement(mca_out)), None)

if not targetless_7_5_measurement:
    raise RuntimeError("Measurment not found")

channel_counts = np.array(targetless_7_5_measurement.channel_count_list) / targetless_7_5_measurement.measurement_time
channel_counts_uncertainty = np.sqrt(channel_counts)

MEASUREMENT_LENGTH = len(channel_counts)

channel_index = np.arange(MEASUREMENT_LENGTH, dtype=np.float32)
channel_uncertainty = np.full([MEASUREMENT_LENGTH], 1./np.sqrt(3))

gaussian_peak_model_data = curve_fitter.ModelData(channel_index[2930-200:2930+200], channel_counts_uncertainty[2930-200:2930+200], channel_counts[2930-200:2930+200], channel_counts_uncertainty[2930-200:2930+200])

beta, sd, chi_sq, p_value = curve_fitter.odr_fit_gaussian(gaussian_peak_model_data, [2930, 100, 40000])
initial_guess_model = curve_fitter.vectorized_gaussian(2930, 100, 40000)
initial_guess_data = initial_guess_model(np.arange(MEASUREMENT_LENGTH, dtype=np.float32))
gaussian_peak_odr_data = curve_fitter.vectorized_gaussian(beta[0], beta[1], beta[2])(np.arange(MEASUREMENT_LENGTH, dtype=np.float32))
print("Gaussian Peak fitting data: ", beta, sd, chi_sq, p_value, "\n")

compton_spectrum_model_data = curve_fitter.ModelData(channel_index[600:2400], channel_counts_uncertainty[600:2400], channel_counts[600:2400], channel_counts_uncertainty[600:2400])
first_gaussian_initial_guess = [900 , 380, np.sum(channel_counts[735:925])*2]
second_gaussian_initial_guess = [1980, 360, np.sum(channel_counts[1900:2080])*2]

print(f"Normalization guesses: {np.sum(channel_counts[735:925])*2}, {np.sum(channel_counts[1900:2080])*2}")
beta, sd, chi_sq, p_value = curve_fitter.odr_fit_two_gaussian_sum(compton_spectrum_model_data, first_gaussian_initial_guess+second_gaussian_initial_guess)
print(f"Compton spectrum fitting data:\nFirst gaussian: values: {beta[0:3]}, errors: {sd[0:3]}\nSecond gaussian: values: {beta[3:]}, errors: {sd[3:]}\nChi-sq: {chi_sq}, p-value: {p_value}")
compton_spectrum_odr_data = curve_fitter.vectorized_two_gaussian_sum(beta)(np.arange(MEASUREMENT_LENGTH, dtype=np.float32))

fig = plotly_utils.generate_scatter_and_line_plot(channel_counts, gaussian_peak_odr_data, compton_spectrum_odr_data)
fig.update_layout(height=800)
fig.show()

background_noise, noise_uncertainty = analysis_utils.find_background_noise(channel_counts[4200:6100])

Gaussian Peak fitting data:  [ 2927.54656851   104.93651132 46784.93067335] [ 0.11047535  0.10303988 42.759325  ] 0.02108790325893657 1.0 

Normalization guesses: 5435.26, 5634.0
Compton spectrum fitting data:
First gaussian: values: [  984.3736844    355.7771356  13854.53620126], errors: [  4.27457214   5.06524425 213.75229392]
Second gaussian: values: [ 1829.36709104   318.96962047 13092.08414216], errors: [  4.29904569   2.71489828 179.92232315]
Chi-sq: 0.058869743912641125, p-value: 1.0


In [10]:
import analysis_utils
model_data = analysis_utils.generate_model_data_from_mca_output(targetless_7_5_measurement)

first_compton_gaussian_guess = curve_fitter.GaussianFittingParameters(900 , 300, np.sum(model_data.y_data[735:925])*4)
second_compton_gaussian_guess = curve_fitter.GaussianFittingParameters(2000, 300, np.sum(model_data.y_data[1900:2080])*4)
main_peak_guess = curve_fitter.GaussianFittingParameters(2930, 100, 48000)

gaussian_sum_model_data = curve_fitter.ModelData(model_data.x_data[MCA_FIRST_NON_ZERO_CHANNEL:], model_data.x_error[MCA_FIRST_NON_ZERO_CHANNEL:], model_data.y_data[MCA_FIRST_NON_ZERO_CHANNEL:], model_data.y_error[MCA_FIRST_NON_ZERO_CHANNEL:])
cs_fitting_datas, cs_uncertainties, chi_sq, p_value  = curve_fitter.odr_fit_gaussian_sum(gaussian_sum_model_data, [first_compton_gaussian_guess, second_compton_gaussian_guess, main_peak_guess])

analysis_utils.print_guassian_sum_fit_output(cs_fitting_datas, cs_uncertainties, chi_sq, p_value)

fitted_line_data = curve_fitter.vectorized_gaussian_sum(cs_fitting_datas)(channel_index)
fig = plotly_utils.generate_scatter_and_line_plot(model_data.y_data, fitted_line_data)

fig.update_layout(height=800)
fig.show()

Gaussian #1: Fitting Params: GaussianFittingParameters(mean=np.float64(878.6049330852377), std_dev=np.float64(280.3532778830761), normalization=np.float64(8894.71825282978)), Uncertainties: (np.float64(13.20508940290369), np.float64(14.924239367718675), np.float64(728.2696661980083))
Gaussian #2: Fitting Params: GaussianFittingParameters(mean=np.float64(1716.947250783145), std_dev=np.float64(439.5502335928257), normalization=np.float64(18325.076619139876)), Uncertainties: (np.float64(19.286997366096696), np.float64(13.409276289070977), np.float64(675.3986192948419))
Gaussian #3: Fitting Params: GaussianFittingParameters(mean=np.float64(2930.48437783922), std_dev=np.float64(111.26845849955406), normalization=np.float64(47298.43484133747)), Uncertainties: (np.float64(0.5761268386237964), np.float64(0.467263425283026), np.float64(241.43987807270236))
Chi sq: 1.1903798074808876, P-Value: 1.0


## Energy Channel Calibration

In [55]:
mca_energy_channel_files = find_mca_files_in_folder(ENERGY_CHANNEL_CALIBRATION_PATH)
mca_outputs = [mca_output.parse_output_file(mca_file) for mca_file in mca_energy_channel_files]

for mca_out_file in mca_outputs:
    fig = plotly_utils.generate_mca_out_figure(mca_out_file, pathlib.Path(mca_out_file.path).stem)
    fig.update_layout(height=600)

    fig.show()

### Ba-133

In [12]:
# Ba-133 Analysis
ba_133_out = next(mca_out for mca_out in mca_outputs if pathlib.Path(mca_out.path).stem == "Ba133")

model_data = analysis_utils.generate_model_data_from_mca_output(ba_133_out)
first_peak_guess = curve_fitter.GaussianFittingParameters(790, 130, sum(model_data.y_data[670:890])*1.4)
second_peak_guess = curve_fitter.GaussianFittingParameters(1325, 100, sum(model_data.y_data[1180:1325])*2.1)
third_peak_guess = curve_fitter.GaussianFittingParameters(1580, 60, sum(model_data.y_data[1580:3003]*1.4))

sliced_data = analysis_utils.slice_model_data(model_data, MCA_FIRST_NON_ZERO_CHANNEL, len(model_data.x_data))
ba_fitting_datas, ba_uncertainties, chi_sq, p_value = curve_fitter.odr_fit_gaussian_sum(sliced_data, [first_peak_guess, second_peak_guess, third_peak_guess])
analysis_utils.print_guassian_sum_fit_output(ba_fitting_datas, ba_uncertainties, chi_sq, p_value)

guess = curve_fitter.vectorized_gaussian_sum([first_peak_guess, second_peak_guess, third_peak_guess])(model_data.x_data)
fitted_line = curve_fitter.vectorized_gaussian_sum(ba_fitting_datas)(model_data.x_data)
fig = plotly_utils.generate_scatter_and_line_plot(model_data.y_data, fitted_line)
fig.update_layout(height=600)
fig.show()

Gaussian #1: Fitting Params: GaussianFittingParameters(mean=np.float64(798.8327216033432), std_dev=np.float64(200.6334159548042), normalization=np.float64(301.8248017460256)), Uncertainties: (np.float64(1.3341927466226806), np.float64(1.9741537188424754), np.float64(2.150231709687516))
Gaussian #2: Fitting Params: GaussianFittingParameters(mean=np.float64(1308.5249568056447), std_dev=np.float64(89.13323073115109), normalization=np.float64(280.3933687974356)), Uncertainties: (np.float64(0.727756150670568), np.float64(0.7423075811026942), np.float64(2.2240281612932815))
Gaussian #3: Fitting Params: GaussianFittingParameters(mean=np.float64(1587.3548815013373), std_dev=np.float64(83.30205333371605), normalization=np.float64(631.6954235203266)), Uncertainties: (np.float64(0.3609134611214316), np.float64(0.28095456394914664), np.float64(2.189940373604511))
Chi sq: 0.004277421175885031, P-Value: 1.0


### Co-60

In [13]:
co_60 = next(mca_out for mca_out in mca_outputs if pathlib.Path(mca_out.path).stem == "Co-60")

model_data = analysis_utils.generate_model_data_from_mca_output(co_60)
first_peak_guess = curve_fitter.GaussianFittingParameters(1084, 800, sum(model_data.y_data[813:1084])*9)
second_peak_guess = curve_fitter.GaussianFittingParameters(3830, 700, sum(model_data.y_data[3830:4400])*4)
third_peak_guess = curve_fitter.GaussianFittingParameters(5109, 173, sum(model_data.y_data[4936:5109])*3)
fourth_peak_guess = curve_fitter.GaussianFittingParameters(5770, 170, sum(model_data.y_data[5770:5940])*3)

sliced_data = analysis_utils.slice_model_data(model_data, MCA_FIRST_NON_ZERO_CHANNEL, len(model_data.x_data))
co_fitting_datas, co_uncertainties, chi_sq, p_value = curve_fitter.odr_fit_gaussian_sum(sliced_data, [first_peak_guess, second_peak_guess, third_peak_guess, fourth_peak_guess])
analysis_utils.print_guassian_sum_fit_output(co_fitting_datas, co_uncertainties, chi_sq, p_value)

guess = curve_fitter.vectorized_gaussian_sum([first_peak_guess, second_peak_guess, third_peak_guess, fourth_peak_guess])(model_data.x_data)
fitted_line = curve_fitter.vectorized_gaussian_sum(co_fitting_datas)(model_data.x_data)
fig = plotly_utils.generate_scatter_and_line_plot(model_data.y_data, fitted_line)
fig.update_layout(height=600)
fig.show()

Gaussian #1: Fitting Params: GaussianFittingParameters(mean=np.float64(1216.0112859025473), std_dev=np.float64(823.6584631102414), normalization=np.float64(677.3781389903161)), Uncertainties: (np.float64(4.326552955954067), np.float64(7.138726452393283), np.float64(5.757868236328959))
Gaussian #2: Fitting Params: GaussianFittingParameters(mean=np.float64(3634.463268092683), std_dev=np.float64(951.2557462819975), normalization=np.float64(605.3650698097888)), Uncertainties: (np.float64(7.098016936541478), np.float64(4.802085280056485), np.float64(3.8316160830959087))
Gaussian #3: Fitting Params: GaussianFittingParameters(mean=np.float64(5090.624882918443), std_dev=np.float64(135.2556759245251), normalization=np.float64(248.37564360264588)), Uncertainties: (np.float64(0.4774181348482929), np.float64(0.4476339726914046), np.float64(0.8839753079913439))
Gaussian #4: Fitting Params: GaussianFittingParameters(mean=np.float64(5763.649441844362), std_dev=np.float64(145.51072494008048), normaliz

### Mn-54

In [14]:
mn_54_out = next(mca_out for mca_out in mca_outputs if pathlib.Path(mca_out.path).stem == "Mn-54")

model_data = analysis_utils.generate_model_data_from_mca_output(mn_54_out)
first_peak_guess = curve_fitter.GaussianFittingParameters(911, 1000, sum(model_data.y_data[911:1843])*3)
second_peak_guess = curve_fitter.GaussianFittingParameters(2610, 400, sum(model_data.y_data[2610:3048])*2)
third_peak_guess = curve_fitter.GaussianFittingParameters(3650, 150, sum(model_data.y_data[3650:3816]*2.5))
fourth_peak_guess = curve_fitter.GaussianFittingParameters(6351, 200, sum(model_data.y_data[6351:6556]*2))

sliced_data = analysis_utils.slice_model_data(model_data, MCA_FIRST_NON_ZERO_CHANNEL, len(model_data.x_data))
mn_fitting_datas, mn_uncertainties, chi_sq, p_value = curve_fitter.odr_fit_gaussian_sum(sliced_data, [first_peak_guess, second_peak_guess, third_peak_guess, fourth_peak_guess])
analysis_utils.print_guassian_sum_fit_output(mn_fitting_datas, mn_uncertainties, chi_sq, p_value)

guess = curve_fitter.vectorized_gaussian_sum([first_peak_guess, second_peak_guess, third_peak_guess, fourth_peak_guess])(model_data.x_data)
fitted_line = curve_fitter.vectorized_gaussian_sum(mn_fitting_datas)(model_data.x_data)
fig = plotly_utils.generate_scatter_and_line_plot(model_data.y_data, fitted_line)
fig.update_layout(height=600)
fig.show()

Gaussian #1: Fitting Params: GaussianFittingParameters(mean=np.float64(-1979.6750654305677), std_dev=np.float64(2596.9867133989233), normalization=np.float64(250.6468655053658)), Uncertainties: (np.float64(184.2604749803146), np.float64(52.16741522087778), np.float64(19.293512167773198))
Gaussian #2: Fitting Params: GaussianFittingParameters(mean=np.float64(2627.086337415332), std_dev=np.float64(156.33269911974222), normalization=np.float64(1.1231023092387333)), Uncertainties: (np.float64(11.398475630969083), np.float64(12.39627147055381), np.float64(0.0901236677335763))
Gaussian #3: Fitting Params: GaussianFittingParameters(mean=np.float64(3655.5141965615144), std_dev=np.float64(108.69823472813754), normalization=np.float64(7.339078309367568)), Uncertainties: (np.float64(1.2926839593605268), np.float64(1.1420103064435392), np.float64(0.08117923844660317))
Gaussian #4: Fitting Params: GaussianFittingParameters(mean=np.float64(6315.063172114676), std_dev=np.float64(148.860098195241), no

In [15]:
na_22_out = next(mca_out for mca_out in mca_outputs if pathlib.Path(mca_out.path).stem == "Na22")

model_data = analysis_utils.generate_model_data_from_mca_output(na_22_out)
first_peak_guess = curve_fitter.GaussianFittingParameters(1000, 300, sum(model_data.y_data[1000:1600])*2)
second_peak_guess = curve_fitter.GaussianFittingParameters(1000, 300, sum(model_data.y_data[1000:1600])*2)
third_peak_guess = curve_fitter.GaussianFittingParameters(2244, 200, sum(model_data.y_data[2244:2444])*2)
fourth_peak_guess = curve_fitter.GaussianFittingParameters(5446, 120, 3)

sliced_data = analysis_utils.slice_model_data(model_data, MCA_FIRST_NON_ZERO_CHANNEL, len(model_data.x_data))
fitting_datas, uncertainties, chi_sq, p_value = curve_fitter.odr_fit_gaussian_sum(sliced_data, [first_peak_guess, second_peak_guess, third_peak_guess, fourth_peak_guess])
analysis_utils.print_guassian_sum_fit_output(fitting_datas, uncertainties, chi_sq, p_value)

guess = curve_fitter.vectorized_gaussian_sum([first_peak_guess, second_peak_guess, third_peak_guess, fourth_peak_guess])(model_data.x_data)
fitted_line = curve_fitter.vectorized_gaussian_sum(fitting_datas)(model_data.x_data)
fig = plotly_utils.generate_scatter_and_line_plot(model_data.y_data, fitted_line)
fig.update_layout(height=600)
fig.show()

Gaussian #1: Fitting Params: GaussianFittingParameters(mean=np.float64(-9520.635881297045), std_dev=np.float64(4476.325122805867), normalization=np.float64(2717.385505512688)), Uncertainties: (np.float64(4813.419225705864), np.float64(796.4095096644998), np.float64(4891.218739583683))
Gaussian #2: Fitting Params: GaussianFittingParameters(mean=np.float64(1141.8611970906281), std_dev=np.float64(378.4312153171589), normalization=np.float64(14.839219951386136)), Uncertainties: (np.float64(24.68350904127363), np.float64(25.50380085721653), np.float64(1.9349656409643725))
Gaussian #3: Fitting Params: GaussianFittingParameters(mean=np.float64(2238.531873545808), std_dev=np.float64(87.23461322714226), normalization=np.float64(20.560870134070264)), Uncertainties: (np.float64(1.040193696719788), np.float64(0.9219982165007473), np.float64(0.23562445437931423))
Gaussian #4: Fitting Params: GaussianFittingParameters(mean=np.float64(5446.1215632646545), std_dev=np.float64(124.70073656834367), norma

### Cs-137

In [69]:
cs_137_out = next(mca_out for mca_out in mca_outputs if pathlib.Path(mca_out.path).stem == "Cs137")

model_data = analysis_utils.generate_model_data_from_mca_output(cs_137_out)
first_peak_guess = curve_fitter.GaussianFittingParameters(1051, 300, sum(model_data.y_data[812:1051])*2)
second_peak_guess = curve_fitter.GaussianFittingParameters(1863, 300, sum(model_data.y_data[1863:2066])*3)
third_peak_guess = curve_fitter.GaussianFittingParameters(2883, 100, sum(model_data.y_data[2883:3000])*3)

sliced_data = analysis_utils.slice_model_data(model_data, MCA_FIRST_NON_ZERO_CHANNEL, len(model_data.x_data))
cs_calib_fitting_datas, cs_calib_uncertainties, chi_sq, p_value = curve_fitter.odr_fit_gaussian_sum(sliced_data, [first_peak_guess, second_peak_guess, third_peak_guess])
analysis_utils.print_guassian_sum_fit_output(cs_calib_fitting_datas, cs_calib_uncertainties, chi_sq, p_value)

guess = curve_fitter.vectorized_gaussian_sum([first_peak_guess, second_peak_guess, third_peak_guess])(model_data.x_data)
fitted_line = curve_fitter.vectorized_gaussian_sum(cs_calib_fitting_datas)(model_data.x_data)
fig = plotly_utils.generate_scatter_and_line_plot(model_data.y_data, fitted_line)
fig.update_layout(height=600)
fig.show()

Gaussian #1: Fitting Params: GaussianFittingParameters(mean=np.float64(949.5878090278054), std_dev=np.float64(367.94458426916555), normalization=np.float64(682.9545585644443)), Uncertainties: (np.float64(9.591798984403171), np.float64(8.804522330423545), np.float64(22.97182417378034))
Gaussian #2: Fitting Params: GaussianFittingParameters(mean=np.float64(1741.9525901931365), std_dev=np.float64(361.3158398157626), normalization=np.float64(491.7662197180332)), Uncertainties: (np.float64(13.973049032418507), np.float64(5.977295766711226), np.float64(19.987522823992904))
Gaussian #3: Fitting Params: GaussianFittingParameters(mean=np.float64(2879.006532006818), std_dev=np.float64(103.41397214982588), normalization=np.float64(1133.405194241617)), Uncertainties: (np.float64(0.22050754119488547), np.float64(0.16463284285624552), np.float64(2.370302989872594))
Chi sq: 0.0048826223745633765, P-Value: 1.0


### Energy Channel Line Fit

In [79]:
# Taken from live chart represents the energies of our various materials
# The order is: ba-133 (1), ba-133 (2), cs-137, mn-54, co-60, co-60
gamma_energy_data = np.array([302.8508, 356.0129, 661.657, 834.848, 1173.228, 1332.492])
gamma_energy_error = np.array([0.0005, 0.0007, 0.003, 0.003, 0.003, 0.004])

channel_expectancy_data = np.array([ba_fitting_datas[1].mean, ba_fitting_datas[2].mean, cs_fitting_datas[2].mean, mn_fitting_datas[2].mean, co_fitting_datas[2].mean, co_fitting_datas[3].mean])
channel_expectancy_error = np.array([ba_uncertainties[1][0], ba_uncertainties[2][0], cs_uncertainties[2][0], mn_uncertainties[2][0], co_uncertainties[2][0], co_uncertainties[3][0]])

energy_channel_model_data = curve_fitter.ModelData(channel_expectancy_data, channel_expectancy_error, gamma_energy_data, gamma_energy_error)
fitted_params, params_uncertainties, chi_sq, p_value = curve_fitter.odr_fit(energy_channel_model_data, curve_fitter.linear_model, [1, 1])

print(f"Fitted line: {fitted_params[0]} + {fitted_params[1]}x")
print(f"Uncertainties: free term: {params_uncertainties[0]}, slope: {params_uncertainties[1]}")
print(f"Chi square: {chi_sq}, P-Value: {p_value}")

energy_channel_fit_model = curve_fitter.vectorized_line(fitted_params[0], fitted_params[1])
energy_channel_fit_data = curve_fitter.vectorized_line(fitted_params[0], fitted_params[1])(np.arange(6000))

fig = plotly_utils.generate_scatter_with_x_and_lines_plot(gamma_energy_data, channel_expectancy_data, energy_channel_fit_data)
fig.show()

Fitted line: -11.046254680237363 + 0.2328944786279174x
Uncertainties: free term: 3.6008072893266254, slope: 0.0009525241538972128
Chi square: 1185.5641411725458, P-Value: 0.0


## Detector Efficiency

In [104]:
# Detector yields for different materials - by yields we simply mean the integral or total counts for a specific gaussian that was fitted earlier
detector_yields = np.array([ba_fitting_datas[1].normalization, ba_fitting_datas[2].normalization, cs_fitting_datas[2].normalization, mn_fitting_datas[2].normalization, co_fitting_datas[2].normalization, co_fitting_datas[3].normalization])
# The measurements were: 8-9 for the diameter of the thing, 68cm for the center of the table, 87cm for the detector, 1cm for the target.
source_to_target_distance = 68
detector_diameter = 9

# The area under the time-normalized gaussian fit in the order of ba-133(1) ba-133(2) cs-137 mn-54 co-60(1) co-60(2)
material_gaussian_area_data = np.array([ba_fitting_datas[1].normalization, ba_fitting_datas[2].normalization, cs_calib_fitting_datas[2].normalization, mn_fitting_datas[2].normalization, co_fitting_datas[2].normalization, co_fitting_datas[3].normalization])
material_gaussian_area_error = np.array([ba_uncertainties[1][2], ba_uncertainties[2][2], cs_calib_uncertainties[2][2], mn_uncertainties[2][2], co_uncertainties[2][2], co_uncertainties[3][2]])

material_theoretical_emission = np.array([379.0077917, 1284.070114, 4452.882399, 57.8903655, 1574.71673144609, 1576.29460392249])
material_theoretical_emission_error = np.array([20.76867116, 70.36380395, 244.0067257, 3.172246035, 86.2905056, 86.37696903])

efficiency = material_gaussian_area_data / material_theoretical_emission
efficiency_errors = efficiency * np.sqrt(np.square(material_gaussian_area_error/material_gaussian_area_data) + np.square(material_theoretical_emission_error/material_theoretical_emission))

material_energy = energy_channel_fit_model(channel_expectancy_data)
material_energy_error = 0.5*(energy_channel_fit_model(channel_expectancy_data + channel_expectancy_error) - energy_channel_fit_model(channel_expectancy_data - channel_expectancy_error))

efficiency_model_data = curve_fitter.ModelData(material_energy, material_energy_error, efficiency, efficiency_errors)
efficiency_guess = (250, 2000)
efficiency_model_guess_line = curve_fitter.vectorized_efficiency_model(efficiency_guess)(np.arange(200, 1600))

efficiency_fit_params, efficiency_fit_uncertainties, chi_sq, p_value = curve_fitter.odr_fit_efficiency(efficiency_model_data, efficiency_guess)

print(f"Efficiency fit, data:\nModel = a/E + b/E^2\nFit params (in the same order as in the model): {efficiency_fit_params}\nUncertainties: {efficiency_fit_uncertainties}\nChi Square: {chi_sq}, P-Value: {p_value}")
efficiency_fit_model = curve_fitter.vectorized_efficiency_model(efficiency_fit_params)(np.arange(200, 1600))

fig = plotly_utils.generate_scatter_with_x_and_lines_plot(efficiency, material_energy, efficiency_fit_model, error_y=efficiency_errors)
fig.update_layout(height=600)

fig.show()

Efficiency fit, data:
Model = a/E + b/E^2
Fit params (in the same order as in the model): [  124.85377961 19937.25880232]
Uncertainties: [   38.88629706 21768.69961016]
Chi Square: 25.545910375967797, P-Value: 3.906638077089131e-05


## Aluminum Target

In [ ]:
aluminum_target_mca_files = find_mca_files_in_folder(r"G:\.shortcut-targets-by-id\1IcR20O5deY8V-HZhJrHf7ZL2cmAiG7GY\ComptonMeasurements\AluminumTarget")
angle_mca_outputs = [mca_output.parse_output_file(mca_out_file) for mca_out_file in aluminum_target_mca_files]
for mca_out in angle_mca_outputs:
    fig = plotly_utils.generate_mca_out_figure(mca_out, pathlib.Path(mca_out.path).stem)
    fig.show()

### Negative 42.5

In [48]:
negative_42_5_mca_out = next(mca_out for mca_out in mca_outputs if pathlib.Path(mca_out.path).stem == "alum_-42.5")

model_data = analysis_utils.generate_model_data_from_mca_output(negative_42_5_mca_out)

# Guesses
#first_gaussian = curve_fitter.GaussianFittingParameters(68.49851487522767, 1305.0935057647634, 319.4731112955267)
second_gaussian = curve_fitter.GaussianFittingParameters(882, 500, 20)
third_gaussian = curve_fitter.GaussianFittingParameters(2052, 179, sum(model_data.y_data[2052-179:2052+179]))
fourth_gaussian = curve_fitter.GaussianFittingParameters(2863, 137, sum(model_data.y_data[2863:3000]*2))

sliced_data = analysis_utils.slice_model_data(model_data, MCA_FIRST_NON_ZERO_CHANNEL, len(model_data.x_data))
fit_datas, uncertainties, chi_sq, p_value = curve_fitter.odr_fit_gaussian_sum(sliced_data, [second_gaussian, third_gaussian, fourth_gaussian])
initial_guess = curve_fitter.vectorized_gaussian_sum([second_gaussian, third_gaussian, fourth_gaussian])(model_data.x_data)
fit = curve_fitter.vectorized_gaussian_sum([fit_datas[0], fit_datas[1], fit_datas[2]])(model_data.x_data)

analysis_utils.print_guassian_sum_fit_output(fit_datas, uncertainties, chi_sq, p_value)

fig = plotly_utils.generate_scatter_and_line_plot(model_data.y_data, fit)
fig.show()

Gaussian #1: Fitting Params: GaussianFittingParameters(mean=np.float64(68.49577370918342), std_dev=np.float64(1305.0951830627503), normalization=np.float64(319.473709538692)), Uncertainties: (np.float64(38.20668300639864), np.float64(12.98047998806992), np.float64(8.115402035285452))
Gaussian #2: Fitting Params: GaussianFittingParameters(mean=np.float64(2043.9960214191294), std_dev=np.float64(175.2695409321779), normalization=np.float64(61.689718976112495)), Uncertainties: (np.float64(0.9883733423425021), np.float64(0.978112310148745), np.float64(0.39002044698211696))
Gaussian #3: Fitting Params: GaussianFittingParameters(mean=np.float64(2854.67758680653), std_dev=np.float64(106.08801694337957), normalization=np.float64(23.74543479859393)), Uncertainties: (np.float64(0.8450494064359864), np.float64(0.7563978774074555), np.float64(0.18216105148368447))
Chi sq: 0.0009400618437722214, P-Value: 1.0
